<a href="https://colab.research.google.com/github/abhijit-z/IDS_506_Omicron_Tweets_Analysis/blob/main/CoRex_Topic_Modeling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## CoReX topic modeling - Unsupervised and Semi-supervised

Performed experimentation with LDA topic modeling as well

## Importing the necessary libraries

In [ ]:
import pandas as pd
import numpy as np
import glob
from datetime import datetime
import os
import re
import string
import nltk

from collections import Counter
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

import seaborn as sns
import matplotlib.pyplot as plt

from datetime import datetime
from datetime import timedelta
from datetime import date

from sklearn.feature_extraction.text import CountVectorizer
import scipy.sparse as ss


from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:

!pip install corextopic

from corextopic import corextopic as ct
from corextopic import vis_topic as vt
#vt.vis_rep(anchored_topic_model, column_label=words, prefix='ZocDoc')

from nltk.tokenize import TweetTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet

In [ ]:
# Setting column width and dataframe display size
pd.set_option("max_colwidth", 300)
pd.set_option("max_columns", 30)
pd.set_option("max_rows", 10000)


In [ ]:
#print(dfx.loc[14]['clean_text'])

## LDA function

In [ ]:
# LDA function
def func_lda(dfs):
  import gensim
  from gensim.utils import simple_preprocess
  import nltk
  nltk.download('stopwords')
  from nltk.corpus import stopwords
  stop_words = stopwords.words('english')
  # stop_words.extend(['from', 'subject', 're', 'edu', 'use'])

  def sent_to_words(sentences):
    for sentence in sentences:
      # deacc=True removes punctuations
      yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))
  def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) 
              if word not in stop_words] for doc in texts]
  def remove_numbs(text2):    # to remove numbers
    return [[word for word in word_set 
              if not word.isdigit()] for word_set in text2]

  data = dfs.values.tolist()
  data_words = list(sent_to_words(data))
  print(type(data_words))
  print("simple output:")
  print(data_words)
  
  # remove stop words
  data_words = remove_stopwords(data_words)
  #print("After removing stopwords:")
  #print(data_words)
  data_words    =  remove_numbs(data_words)           

  print(data_words[:1][0][:30])
  
  
  
  import gensim
  from gensim.models import CoherenceModel
  import gensim.corpora as corpora
  # Create Dictionary

  id2word = corpora.Dictionary(data_words)

  # Create Corpus
  texts = data_words
  # Term Document Frequency
  corpus = [id2word.doc2bow(text) for text in texts]
  # View
  print("corpus output:")
  print(corpus[:1][0][:30])

  from pprint import pprint

  # number of topics
  num_topics = 10

  # Build LDA model
  lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                        id2word=id2word,
                                        num_topics=num_topics)

  # Print the Keyword in the 10 topics
  print("topics:")
  pprint(lda_model.print_topics())
  doc_lda = lda_model[corpus]
  
  return (num_topics,id2word,corpus,lda_model)


## Unsupervised CoRex function

In [ ]:
def corex_func(df2):
  #from sklearn.feature_extraction.text import CountVectorizer
  cv = CountVectorizer(max_df=0.95, min_df=2, stop_words='english')
  dtm = cv.fit_transform(df2['lemma_2'])

  # Get words that label the columns (needed to extract readable topics and make anchoring easier)
  words = list(np.asarray(cv.get_feature_names()))

  print(words)

  print(type(words))
  
  not_digit_inds = [ind for ind, word in enumerate(words) if not word.isdigit()]
  dtm = dtm[:, not_digit_inds]
  words    = [word for ind,word in enumerate(words) if not word.isdigit()]

  print(dtm.shape)
  
  anchors = [] #without seed words
  anchors = [
      [a for a in topic if a in words]
      for topic in anchors
          ]

  model = ct.Corex(n_hidden=14, seed=51)
  model = model.fit(
      dtm,
      words=words,
      anchors = anchors,
      anchor_strength=10)

  for i, topic_ngrams in enumerate(model.get_topics(n_words=20)):
      topic_ngrams = [ngram[0] for ngram in topic_ngrams if ngram[1] > 0]
      print("Topic #{}: {}".format(i+1, ", ".join(topic_ngrams)))


  

In [ ]:
#symptoms,causes,transmission,prevention,testing,treatment,mental_health,economic_impact,vaccination,vaccination_opposition, policies,children_education,government

## Semi-supervised CoRex function

In [ ]:
# Topics and Anchor words
#Set2

anchor_words = [
#1 symptoms =  
['cold', 'cough', 'flu',  'fever', 'headache', 'sore', ' throat', 'muscle', 'breath', 'lungs',
             'nausea', 'vomit', 'diarrhea', 'fever', 'fatigue', 'tired', 'symptom','mild','disease','reinfection', 'illness'],
#2 prevention = 
['mask', 'sanitizer', 'distance', 'glove', 'ppe', 'kit', 'n95', 'quarantine' ,'wash', 'isolation', 'wearamask', 'maskup', 'kn95'],
#3 testing = 
['test', 'positive', 'negative', 'oximeter', 'pcr', 'rtpcr', 'detect','report'],
#4 treatment = 
['antibody','sotrovimab','therapy','antigen','bamlanivimab','etesevimab','casirivimab','imdevimab','regen','sotrovimab',
             'tixagevimab','cilgavimab','evusheld','medication','acetaminophen','ibuprofen','pharmacy','capsule','tablet','ayurveda',
             'reliever','ivermectin','pill', 'injection', 'doctor', 'mrna', 'monoclonal', 'icu'],

#5 economic_impact =  
['economic', 'stock', 'market', 'layoff', 'unemployed', 'job', 'interview', 'poor', 'wage', 'salary', 'finance', 'closure',
                   'price','investor', 'crypto', 'bitcoin', 'inflation'],
#6 Travel = 
['travel', 'flight', 'cab', 'train', 'bus', 'metro', 'publictransport', 'holiday', 'vacation', 'passenger', 'arrival', 'departure', 
          'cruise', 'ship', 'airport','drive'],
#7 vaccination = 
['pfizer','biontech','johnson','vaccine','moderna','niaid','covishield','covaxin','jabbed','vaxxed','vax','protection','booster',
               'vaccinate', 'getboostednow', 'dose', 'sciencewins', 'getvaccinatednow', 'covaxin4kids', 'superimmunity'],
#8 vaccination_opposition =
['conspiracy','unvaccinated','chip','anti','antivax','vaccinekills','novaccincation','justsayno',
                          'boycottvaccine','saynotovaccine', 'vaccinesideeffects', 'covidiots', 'donotcomply'],
#9 policies = 
['mandate','rule','regulation','policy','lockdown','suspend','ban', 'mandatory','restriction','impose','guideline','measure', 
            'safetyfirst', 'letitrip', 'vaccinepassports'],
#10 causes = 
['party','crowd','marriage','gathering','concert','game','event','movie','wedding','function','marathon','conference',
          'match','football'],
#11 transmission = 
['contagious','spread','transmit','touch','case','infect','mutate', 'mutation', 'outbreak','airborne','droplets','superspreader', 'death'],
#12 children_education = 
['school','college','children','education','college','university','maketerm1hybird','cancelterm1','exam', 'institute', 'semester',
		       'teacher', 'class', 'classroom'],
#13 government = 
['official','federal','state','president','minister','government','misinformation','authority', 'pm', 'premier'],

#14 mental_health = 
['stress', 'depress', 'lonely', 'sad', 'anxiety', 'alert', 'panic']
]

all_topics = ['symptoms','prevention', 'testing', 'treatment', 'economic_impact', 'travel', 'vaccination', 'vaccination_opposition', 
 'policies', 'causes', 'transmission', 'children_education', 'government', 'mental_health']

# Semi Supervised CoRex function

def corex_func_anchor(df2):
  #from sklearn.feature_extraction.text import CountVectorizer
  cv = CountVectorizer(max_df=0.95, min_df=2, stop_words='english')
  dtm = cv.fit_transform(df2['lemma_2'])
  print(type(dtm))
  print(dtm.shape, "\n")
  # Get words that label the columns (needed to extract readable topics and make anchoring easier)
  words = list(np.asarray(cv.get_feature_names()))
  
  not_digit_inds = [ind for ind,word in enumerate(words) if not word.isdigit()]
  dtm = dtm[:, not_digit_inds]
  words    = [word for ind,word in enumerate(words) if not word.isdigit()]

  print(dtm.shape)
  print("\n")
  #print(dtm.head)

  
  anchors = [
      [a for a in topic if a in words]
      for topic in anchor_words
          ]
  print("THESE ARE THE ANCHORS")
  print(anchors)

  model = ct.Corex(n_hidden=len(all_topics), seed=37)
  model = model.fit(
      dtm,
      words=words,
      anchors = anchors,
      anchor_strength=10)

  for i, topic_ngrams in enumerate(model.get_topics(n_words=30)):
      topic_ngrams = [ngram[0] for ngram in topic_ngrams if ngram[1] > 0]
      print("Topic #{}: {}".format(i+1, ", ".join(topic_ngrams)))
  
  vt.vis_rep(model, column_label=words)

  #Total Correlation score for each topic on all tweets
  print(model.tcs)
  print("\n")

  print(model.p_y_given_x)
  print("\n")

  #probability a document (row) belongs to a certain topic where 0 is 100% probability
  #The closer to zero the more likely that row/review/document belongs to that topic
  
  #print(model.log_p_y_given_x)
  
  log_table = model.log_p_y_given_x
  return log_table, words 

  #print("\n")


  
  #Here model is the the corex model defined above, we extract the log_z score, 
  #which represents the strength of a topic relative to the document (long string of concatnated tweets) 

  #variable a holds the object below
  ''' 
  a = model.log_z

  #Defining the schema for the dataframe which builds on tabluating the results for topic strength
  twt = list(df2['id'])
  col = ['symptoms','prevention','testing','treatment','mental_health','economic_impact','vaccination', 
         'vaccination_opposition', 'policies', 'causes', 'transmission', 'children+Education', 'government']

  #Define the dataframe with above schema and fill in the topic strength values 'a' for the corresponding topics and twitter handles
  cor = pd.DataFrame(a, columns=col)

  cor['id'] = list(df2['id'])

  cor

  return cor
  '''



In [ ]:
'''
path = "/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv"
dfy = pd.read_csv(path, engine='python')
dfy.shape
'''


'\npath = "/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv"\ndfy = pd.read_csv(path, engine=\'python\')\ndfy.shape\n'

## Reading and clubbing the weekly csv files into one dataframe

In [ ]:

#dft = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv", engine ='python')
#dft = pd.DataFrame(columns = dft.columns)
#dft.head(1000)


In [ ]:
df = pd.read_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter6_res/Vader_OP/V_Sentiment_Week1.csv", engine ='python')
df.columns
#df = pd.DataFrame(columns = df.columns + )

Index(['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos'],
      dtype='object')

In [ ]:
df.head()

created_at                   id  \
0  Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1  Fri Nov 26 16:11:42 +0000 2021  1464265614994952199   
2  Fri Nov 26 17:58:39 +0000 2021  1464292531970220036   
3  Fri Nov 26 17:58:37 +0000 2021  1464292524667854852   
4  Fri Nov 26 17:58:35 +0000 2021  1464292515901677570   

                                                                                                                                                                                                                 text  \
0  It was so nice to join @UBCAOII for initiation - the first in person one the chapter has held since the world closed down because of #COVID19 @alphaomicronpi @aoiivancouver @AOII_Calgary https://t.co/3ApQZofbHM   
1                                                                                                New Nu Novel Coronavirus SARS-CoV2 COVID-19 variant.\n\nCouldn’t be easy like Kappa or Lambda or Omicron or even Pi.   
2                                                                                                                                              PUT AWAY THE "Nu" jokes - the name is Omicron. https://t.co/CgsZlzK4Cw   
3                                                                                                             @RiochtConor2 BREAKING: WHO designates new coronavirus strain as a variant of concern, names it Omicron   
4                                                                                                                                                                                     Omicron https://t.co/m2vLDtse5L   

        user_id  \
0  1.634359e+07   
1  1.754451e+07   
2  4.321370e+07   
3  2.719413e+07   
4  1.336693e+18   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos  
0    0.7253  0.000  0.7

In [ ]:

#df = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv", engine ='python')
df = pd.DataFrame(columns = ['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos', 'week'])


interesting_files = glob.glob("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter6_res/Vader_OP/*.csv")  
#print(len(interesting_files))
number_of_files = len(interesting_files)

for week in range(1, number_of_files+1):    # number_of_files
  path = "/content/drive/MyDrive/Omicron Tweet Analytics project/Filter6_res/Vader_OP/V_Sentiment_Week" + str(week) + ".csv"
  dfx = pd.read_csv(path, engine= 'python')
  dfx['week'] = "week_" + str(week)
  df = pd.concat([df, dfx], ignore_index=True)  

df['id'] = df['id'].astype(str)
df.shape

(441776, 11)

In [ ]:
one_to_hundred = pd.Series(range(1,len(df)+1))
df['UIN'] = one_to_hundred

In [ ]:
df.tail()

created_at                   id  \
441771  Tue Feb 01 05:02:03 +0000 2022  1488377083076263936   
441772  Tue Feb 01 05:02:09 +0000 2022  1488377106992033797   
441773  Tue Feb 01 05:03:18 +0000 2022  1488377396805836803   
441774  Tue Feb 01 05:02:19 +0000 2022  1488377149308481542   
441775  Tue Feb 01 05:04:44 +0000 2022  1488377756526206976   

                                                                                                                                                                                                                                                           text  \
441771                                                                                                                                  Ivermectin Has 'Antiviral Effect' Against Omicron And All Other 'Mutant Strains' Of Covid-19\n\nhttps://t.co/t7zACadkNP   
441772                                                                                                                     @realDailyWire CORRECTED-Japan's Kowa says ivermectin showed 'antiviral effect' against Omicron in research\nhttps://t.co/gZeVT8t9CZ   
441773                                                                                                                                                         2 new omicron symptoms you won’t realize are from COVID https://t.co/9yweO1KuKG via @DeseretNews   
441774                                                                   COVID-19 Omicron variant now dominant in Italy, health body says - Reuters\n\nPublished At :2022-01-14T12:09:00Z\nSource:"#Reuters"\n\nhttps://t.co/srhWh9hcLW https://t.co/QqSpqPYMl2   
441775  Good grief . . . Where’s the logic in this @ShabirMadh @Tuliodna . . . ‘South Africans who test positive for the coronavirus but show no symptoms of Covid-19 will no longer be required to self-isolate’ \n#covid #Omicron \n\nhttps://t.co/OwHxpGuQZz   

             user_id  \
441771  9.821061e+17   
441772  2.855330e+09   
441773  1.521389e+08   
441774  1.441500e+18   
441775  1.218511e+08   

                                                                                                                                                                                                                                                omicron_tweets  \
441771                                                                                                                                 ivermectin has 'antiviral effect' against omicron and all other 'mutant strains' of covid-19\n\nhttps://t.co/t7zacadknp   
441772                                                                                                                    @realdailywire corrected-japan's kowa says ivermectin showed 'antiviral effect' against omicron in research\nhttps://t.co/gzevt8t9cz   
441773                                                                                                                                                        2 new omicron symptoms you won’t realize are from covid https://t.co/9yweo1kukg via @deseretnews   
441774                                                                  covid-19 omicron variant now dominant in italy, health body says - reuters\n\npublished at :2022-01-14t12:09:00z\nsource:"#reuters"\n\nhttps://t.co/srhwh9hclw https://t.co/qqspqpyml2   
441775  good grief . . . where’s the logic in this @shabirmadh @tuliodna . . . ‘south africans who test positive for the coronavirus but show no symptoms of covid-19 will no longer be required to self-isolate’ \n#covid omicron \n\nhttps://t.co/owhxpguqzz   

                                                                                                                                                                                           clean_text  \
441771                                                                                                      ivermectin has antiviral effect against omicron and all other mutant strains of covid19    

In [ ]:
df.isnull().sum()

created_at          2
id                  0
text               27
user_id            30
omicron_tweets     27
clean_text         76
compound          125
neg               125
neu               125
pos               125
week                0
UIN                 0
dtype: int64

In [ ]:
df = df.dropna()
print(df.shape)
df.isnull().sum()


(441648, 12)


created_at        0
id                0
text              0
user_id           0
omicron_tweets    0
clean_text        0
compound          0
neg               0
neu               0
pos               0
week              0
UIN               0
dtype: int64

In [ ]:
#df = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv", engine ='python')
# 1464292750883319813

In [ ]:
df.head(1000)

created_at                   id  \
0    Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1    Fri Nov 26 16:11:42 +0000 2021  1464265614994952199   
2    Fri Nov 26 17:58:39 +0000 2021  1464292531970220036   
3    Fri Nov 26 17:58:37 +0000 2021  1464292524667854852   
4    Fri Nov 26 17:58:35 +0000 2021  1464292515901677570   
5    Fri Nov 26 17:59:04 +0000 2021  1464292636521644045   
6    Fri Nov 26 17:59:13 +0000 2021  1464292675553742854   
7    Fri Nov 26 17:59:05 +0000 2021  1464292642808815622   
8    Fri Nov 26 17:58:46 +0000 2021  1464292561443512325   
9    Fri Nov 26 17:59:06 +0000 2021  1464292644507504645   
10   Fri Nov 26 17:58:58 +0000 2021  1464292612207263759   
11   Fri Nov 26 17:59:15 +0000 2021  1464292681413275653   
12   Fri Nov 26 17:59:28 +0000 2021  1464292736312516618   
13   Fri Nov 26 17:59:31 +0000 2021  1464292750883319813   
14   Fri Nov 26 17:59:32 +0000 2021  1464292753366528002   
15   Fri Nov 26 17:59:28 +0000 2021  1464292737570775041   
16   Fri Nov 26 17:59:21 +0000 2021  1464292710022623239   
17   Fri Nov 26 17:59:22 +0000 2021  1464292713688358914   
18   Fri Nov 26 17:59:43 +0000 2021  1464292799025668111   
19   Fri Nov 26 17:59:57 +0000 2021  1464292859557957635   
20   Fri Nov 26 17:59:58 +0000 2021  1464292865308303377   
21   Fri Nov 26 18:00:02 +0000 2021  1464292879556399112   
22   Fri Nov 26 18:00:01 +0000 2021  1464292876427444245   
23   Fri Nov 26 18:00:13 +0000 2021  1464292924347371521   
24   Fri Nov 26 18:00:35 +0000 2021  1464293020044443649   
25   Fri Nov 26 18:00:39 +0000 2021  1464293034531581953   
26   Fri Nov 26 18:00:39 +0000 2021  1464293037241036804   
27   Fri Nov 26 18:01:04 +0000 2021  1464293138596605955   
28   Fri Nov 26 18:01:07 +0000 2021  1464293153901629450   
29   Fri Nov 26 18:01:04 +0000 2021  1464293139259301890   
30   Fri Nov 26 18:01:30 +0000 2021  1464293251129786380   
31   Fri Nov 26 18:01:44 +0000 2021  1464293306293096451   
32   Fri Nov 26 18:01:43 +0000 2021  1464293303533375497   
33   Fri Nov 26 18:01:31 +0000 2021  1464293251721031683   
34   Fri Nov 26 18:01:33 +0000 2021  1464293262064291852   
35   Fri Nov 26 18:01:35 +0000 2021  1464293271337783301   
36   Fri Nov 26 18:01:49 +0000 2021  1464293329797988352   
37   Fri Nov 26 18:02:00 +0000 2021  1464293373800423428   
38   Fri Nov 26 18:02:22 +0000 2021  1464293468096897024   
39   Fri Nov 26 18:01:54 +0000 2021  1464293349167411202   
40   Fri Nov 26 18:02:56 +0000 2021  1464293608685809665   
41   Fri Nov 26 18:03:22 +0000 2021  1464293717322444809   
42   Fri Nov 26 18:03:12 +0000 2021  1464293676188770304   
43   Fri Nov 26 18:03:13 +0000 2021  1464293682857889794   
44   Fri Nov 26 18:03:27 +0000 2021  1464293741531959301   
45   Fri Nov 26 18:03:14 +0000 2021  1464293685143687173   
46   Fri Nov 26 18:03:10 +0000 2021  1464293667569549314   
47   Fri Nov 26 18:03:04 +0000 2021  1464293641699135496   
48   Fri Nov 26 18:03:33 +0000 2021  1464293763820445698   
49   Fri Nov 26 18:04:10 +0000 2021  1464293918325952513   
50   Fri Nov 26 18:04:09 +0000 2021  1464293916191207425   
51   Fri Nov 26 18:03:47 +0000 2021  1464293825648766983   
52   Fri Nov 26 18:03:57 +0000 2021  1464293863921577986   
53   Fri Nov 26 18:03:46 +0000 2021  1464293821005582344   
54   Fri Nov 26 18:04:33 +0000 2021  1464294017919688705   
55   Fri Nov 26 18:04:33 +0000 2021  1464294014660890630   
56   Fri Nov 26 18:04:13 +0000 2021  1464293933438095370   
57   Fri Nov 26 18:05:13 +0000 2021  1464294182823022599   
58   Fri Nov 26 18:05:26 +0000 2021  1464294238775087109   
59   Fri Nov 26 18:05:26 +0000 2021  1464294237437108227   
60   Fri Nov 26 18:05:31 +0000 2021  1464294259918393348   
61   Fri Nov 26 18:06:14 +0000 2021  1464294441892601862   
62   Fri Nov 26 18:05:56 +0000 2021  1464294365816258564   
63   Fri Nov 26 18:05:52 +0000 2021  1464294348863033347   
64   Fri Nov 26 18:06:03 +0000 2021  1464294393339432961   
65   Fri Nov 26 18:05:50 +0000 2021  1464294339971059717   
66   

In [ ]:
# suppressing the scientific notation for id number
#df['id'] = df['id'].apply(lambda x: '%.0f' % x)
#df['id'] = "{:.18f}". format(df['id'])
#type(df['id'][0])

In [ ]:
df.tail(1500)

created_at                   id  \
440276  Mon Jan 31 18:58:27 +0000 2022  1488225181948514307   
440277  Mon Jan 31 18:58:09 +0000 2022  1488225105838702592   
440278  Mon Jan 31 18:58:58 +0000 2022  1488225310873047040   
440279  Mon Jan 31 19:00:21 +0000 2022  1488225658614337536   
440280  Mon Jan 31 19:00:34 +0000 2022  1488225714289745926   
440281  Mon Jan 31 19:00:36 +0000 2022  1488225722988564480   
440282  Mon Jan 31 19:01:51 +0000 2022  1488226035565056009   
440283  Mon Jan 31 19:01:54 +0000 2022  1488226047208345607   
440284  Mon Jan 31 19:02:17 +0000 2022  1488226144168169475   
440285  Mon Jan 31 19:02:24 +0000 2022  1488226172336951296   
440286  Mon Jan 31 19:03:03 +0000 2022  1488226338209214464   
440287  Mon Jan 31 19:03:36 +0000 2022  1488226477619437568   
440288  Mon Jan 31 19:04:22 +0000 2022  1488226669399658499   
440289  Mon Jan 31 19:04:55 +0000 2022  1488226808378003459   
440290  Mon Jan 31 19:06:09 +0000 2022  1488227119238942720   
440291  Mon Jan 31 19:06:01 +0000 2022  1488227085013241858   
440292  Mon Jan 31 19:05:53 +0000 2022  1488227052843003906   
440293  Mon Jan 31 19:06:02 +0000 2022  1488227088930910209   
440294  Mon Jan 31 19:07:13 +0000 2022  1488227386810413059   
440295  Mon Jan 31 19:07:05 +0000 2022  1488227352668631046   
440296  Mon Jan 31 19:06:22 +0000 2022  1488227171789324289   
440297  Mon Jan 31 19:07:20 +0000 2022  1488227416241852418   
440298  Mon Jan 31 19:06:31 +0000 2022  1488227210465275904   
440299  Mon Jan 31 19:08:08 +0000 2022  1488227617274621953   
440300  Mon Jan 31 19:08:32 +0000 2022  1488227715874500609   
440301  Mon Jan 31 19:07:34 +0000 2022  1488227473435287556   
440302  Mon Jan 31 19:09:02 +0000 2022  1488227844798906370   
440303  Mon Jan 31 19:09:20 +0000 2022  1488227920728498179   
440304  Mon Jan 31 19:10:22 +0000 2022  1488228180259446784   
440305  Mon Jan 31 19:09:47 +0000 2022  1488228030837243906   
440306  Mon Jan 31 19:09:51 +0000 2022  1488228050961514496   
440307  Mon Jan 31 19:11:28 +0000 2022  1488228456416493568   
440308  Mon Jan 31 19:11:41 +0000 2022  1488228509633769472   
440309  Mon Jan 31 19:11:21 +0000 2022  1488228428411248641   
440310  Mon Jan 31 19:11:28 +0000 2022  1488228457280638980   
440311  Mon Jan 31 19:11:45 +0000 2022  1488228528323809284   
440312  Mon Jan 31 19:12:42 +0000 2022  1488228767541649409   
440313  Mon Jan 31 19:12:46 +0000 2022  1488228784511799304   
440314  Mon Jan 31 19:12:41 +0000 2022  1488228762865049606   
440315  Mon Jan 31 19:12:42 +0000 2022  1488228765708734476   
440316  Mon Jan 31 19:12:25 +0000 2022  1488228696859287552   
440317  Mon Jan 31 19:12:43 +0000 2022  1488228772155469834   
440318  Mon Jan 31 19:13:02 +0000 2022  1488228851822084099   
440319  Mon Jan 31 19:13:36 +0000 2022  1488228991353851904   
440320  Mon Jan 31 19:13:02 +0000 2022  1488228851675283457   
440321  Mon Jan 31 19:13:26 +0000 2022  1488228952686665728   
440322  Mon Jan 31 19:13:56 +0000 2022  1488229078771838976   
440323  Mon Jan 31 19:14:40 +0000 2022  1488229259395366912   
440324  Mon Jan 31 19:14:31 +0000 2022  1488229225438007305   
440325  Mon Jan 31 19:15:13 +0000 2022  1488229400277487619   
440326  Mon Jan 31 19:15:09 +0000 2022  1488229384586919937   
440327  Mon Jan 31 19:15:52 +0000 2022  1488229561766535169   
440328  Mon Jan 31 19:17:16 +0000 2022  1488229914893553664   
440329  Mon Jan 31 19:16:56 +0000 2022  1488229830118178817   
440330  Mon Jan 31 19:17:08 +0000 2022  1488229882358386698   
440331  Mon Jan 31 19:17:09 +0000 2022  1488229887257239552   
440332  Mon Jan 31 19:17:30 +0000 2022  1488229975799050247   
440333  Mon Jan 31 19:18:28 +0000 2022  1488230215918981121   
440334  Mon Jan 31 19:19:01 +0000 2022  1488230356645859329   
440335  Mon Jan 31 19:18:57 +0000 2022  1488230338392432642   
440336  Mon Jan 31 19:18:37 +0000 2022  1488230256385400835   
440337  Mon Jan 31 19:19:07 +0000 2022  1488230382004625408   
440338  Mon Jan 31 19:20:58 +0000 2022  1488230844904792065

In [ ]:
# Cleaning and lemmatization

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

STOP_WORDS = stopwords.words()

#remove_punc = "\"#$%&'()+,-./:;<=>?@[\]^_`{|}~"     # we kept ! and * because they are used by people to express sentiments


#df = df[['UIN', 'week', 'created_at', 'id', 'omicron_tweets', 'clean_text', 'compound', 'neg' , 'neu' ,'pos']]

print(df.shape)


EMOJI_PATTERN = re.compile("["
                          u"\U0001F600-\U0001F64F"  # emoticons
                          u"\U0001F300-\U0001F5FF"  # symbols & pictographs
                          u"\U0001F680-\U0001F6FF"  # transport & map symbols
                          u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
                          u"\U00002702-\U000027B0"
                          u"\U000024C2-\U0001F251"
                          "]+", flags=re.UNICODE)

def cleaning(text):
  '''
  Convert to lowercase.
  Rremove URL links, special characters and punctuation.
  Tokenize and remove stop words.
  '''
  text = text.lower()
  text = re.sub('https?://\S+|www\.\S+', '', text)
  text = re.sub('@[A-Za-z0-9]+', '', text)
  text = re.sub('<.*?>+', '', text)   # replacing HTML text with blank or whitespace
  
  #text_try = re.sub(r'[^\w\s]', '', text_try)
  #dtext = re.sub('[%s]' % re.escape(remove_punc), '', text)
  text = re.sub('\n', " ", text)
  text = re.sub('[%s]' % re.escape(string.punctuation), '', text)     
  # removes the puncutation characters. re.escape is used to escape the special characters that form puncuation characters. 
  #For eg, \" considers quote as character because of backslash
  text = re.sub('[’“”…]', '', text)
  
  text = text.encode("ascii", "ignore")     # consider only english alphanumeric characters
  text = text.decode()
  
  text = EMOJI_PATTERN.sub(r'', text)



  # removing the stop-words
  text_tokens = word_tokenize(text)
  tokens_without_sw = [
    word for word in text_tokens if not word in STOP_WORDS]
  filtered_sentence = (" ").join(tokens_without_sw)
  text = filtered_sentence

  return text

    
  
def lemmatizer(text_list):
  lmtzr = WordNetLemmatizer()
  lemm_tokens = [lmtzr.lemmatize(word) for word in text_list] #[lmtzr.lemmatize(word) for word in lst]
  lemmatized_text = (" ").join(lemm_tokens)
  text = lemmatized_text
  return text

# POS_TAGGER_FUNCTION : TYPE 1
def pos_tagger(nltk_tag):
  if nltk_tag.startswith('J'):
      return wordnet.ADJ
  elif nltk_tag.startswith('V'):
      return wordnet.VERB
  elif nltk_tag.startswith('N'):
      return wordnet.NOUN
  elif nltk_tag.startswith('R'):
      return wordnet.ADV
  else:         
      return None

def lemma3(clean_txt):
  pos_tagged = nltk.pos_tag(nltk.word_tokenize(clean_txt))
  wordnet_tagged = list(map(lambda x: (x[0], pos_tagger(x[1])), pos_tagged))

  lemmatized_sentence = []
  lmtzr = WordNetLemmatizer()
  for word, tag in wordnet_tagged:
    if tag is None:
    # if there is no available tag, append the token as is
      lemmatized_sentence.append(word)
    else:       
    # else use the tag to lemmatize the token
      lemmatized_sentence.append(lmtzr.lemmatize(word, tag))
  lemmatized_sentence = " ".join(lemmatized_sentence)
  return lemmatized_sentence

def remove_covid(lemm_text):
  lemm_text = re.sub('covid', '', lemm_text)
  lemm_text = re.sub('coronavirus', '', lemm_text)
  lemm_text = re.sub('corona', '', lemm_text)
  lemm_text = re.sub('variant', '', lemm_text)
  lemm_text = re.sub('omicron', '', lemm_text)
  return lemm_text


  



#if __name__ == "__main__":
#    max_rows = 1000  # 'None' to read whole file
    
df['clean_text'] = df['clean_text'].astype(str)
#df_reduced.head() 

#dt = df_reduced['name_plus_desp'].apply(cleaning)
df['clean_text2'] = df['clean_text'].apply(cleaning)



tt = TweetTokenizer()
df['tokenised_tweet'] = df['clean_text2'].apply(tt.tokenize)
#print(test)

df['lemmatized'] = df['tokenised_tweet'].apply(lemmatizer)

df['lemma_2'] = df['clean_text2'].apply(lemma3)

df.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/final_clean_tweets.csv", index=False)




#func_lda(df['lemma_2'])   LDA showed poor results. Hence, filtered tweets for applying LDA
# LDA applied on 'lemma_3' text

df['lemma_3'] = df['lemma_2'].apply(remove_covid)

print("\n")

#num_topics,id2word,corpus,lda_model = func_lda(df['lemma_3'])


#dtm.shape # n_docs x m_words

#dtm
#df.head(900)



[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
(441648, 12)




In [ ]:
df.head()

created_at                   id  \
0  Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1  Fri Nov 26 16:11:42 +0000 2021  1464265614994952199   
2  Fri Nov 26 17:58:39 +0000 2021  1464292531970220036   
3  Fri Nov 26 17:58:37 +0000 2021  1464292524667854852   
4  Fri Nov 26 17:58:35 +0000 2021  1464292515901677570   

                                                                                                                                                                                                                 text  \
0  It was so nice to join @UBCAOII for initiation - the first in person one the chapter has held since the world closed down because of #COVID19 @alphaomicronpi @aoiivancouver @AOII_Calgary https://t.co/3ApQZofbHM   
1                                                                                                New Nu Novel Coronavirus SARS-CoV2 COVID-19 variant.\n\nCouldn’t be easy like Kappa or Lambda or Omicron or even Pi.   
2                                                                                                                                              PUT AWAY THE "Nu" jokes - the name is Omicron. https://t.co/CgsZlzK4Cw   
3                                                                                                             @RiochtConor2 BREAKING: WHO designates new coronavirus strain as a variant of concern, names it Omicron   
4                                                                                                                                                                                     Omicron https://t.co/m2vLDtse5L   

        user_id  \
0  1.634359e+07   
1  1.754451e+07   
2  4.321370e+07   
3  2.719413e+07   
4  1.336693e+18   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos    week  UIN  \
0    0.72

## Reading the stored cleaned tweet file

In [ ]:
#df.isnull().sum()
#df.shape

In [ ]:
df_cleanT = pd.read_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/final_clean_tweets.csv", engine= 'python')

In [ ]:
df_cleanT.columns

In [ ]:

df_cleanT.tail()

In [ ]:
print(df_cleanT.shape)
df_cleanT.isnull().sum()

In [ ]:
df_cleanT[df_cleanT.isnull().any(axis=1)]

created_at            id  \
256032  Mon Dec 27 21:05:00 +0000 2021  1.475573e+18   

                                                                                                         text  \
256032  Thosehttps://www.deseret.com/coronavirus/2021/12/27/22855385/omicron-variant-more-contagious-dr-fauci   

            user_id  \
256032  478295779.0   

                                                                                               omicron_tweets  \
256032  thosehttps://www.deseret.com/coronavirus/2021/12/27/22855385/omicron-variant-more-contagious-dr-fauci   

       clean_text  compound  neg  neu  pos    week     UIN clean_text2  \
256032      those       0.0  0.0  1.0  0.0  week_6  256119         NaN   

       tokenised_tweet lemmatized lemma_2  
256032              []        NaN     NaN

In [ ]:
df_cleanT = df_cleanT.dropna()

In [ ]:
df_cleanT.isnull().sum()

created_at         0
id                 0
text               0
user_id            0
omicron_tweets     0
clean_text         0
compound           0
neg                0
neu                0
pos                0
week               0
UIN                0
clean_text2        0
tokenised_tweet    0
lemmatized         0
lemma_2            0
dtype: int64

In [ ]:
df_cleanT.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/final_clean_tweets2.csv", index=False)

In [ ]:
df_cleanT.info()

In [ ]:
df_cleanT['id'] = df_cleanT['id'].astype(str)

In [ ]:
df_cleanT.head()

## LDA implementation

In [ ]:
!pip install pyLDAvis==3.2.2
# !pip install pickle
!pip install gensim

In [ ]:

'''
import pyLDAvis.gensim
# import pyLDAvis.gensim as gensimvis
import pickle 
import pyLDAvis

# Visualize the topics
pyLDAvis.enable_notebook()
LDAvis_data_filepath = os.path.join('/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/lda_results/ldavis_prepared_'+str(num_topics))

# # this is a bit time consuming - make the if statement True
# # if you want to execute visualization prep yourself
if 1 == 1:
    LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
    with open(LDAvis_data_filepath, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)

# load the pre-prepared pyLDAvis data from disk
with open(LDAvis_data_filepath, 'rb') as f:
    LDAvis_prepared = pickle.load(f)
pyLDAvis.save_html(LDAvis_prepared, '/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/lda_results/ldavis_prepared_'+ str(num_topics) +'.html')
LDAvis_prepared
'''

## Unsupervised CoRex result

In [ ]:
# Unsupervised CoRex
print("\n")

corex_func(df_cleanT)

print("\n")



## Semi-Supervised CoRex results

Correlation Explanation (CorEx) is a topic model that yields rich topics that are maximally 
informative about a set of documents. 
It classifies the text into topics.

Each topic explains a certain portion of the total correlation (TC). 
We can access the topic TCs through the tcs attribute, as well as the overall TC .

CorEx instead estimates the probability a document belongs to a topic given that document's words. 
As a result, the probabilities across topics for a given document do not have to add up to 1. 
The estimated probabilities of topics for each document can be accessed through 
log_p_y_given_x or p_y_given_x.






In [ ]:
#df.isnull().sum()

In [ ]:
df_cleanT.isnull().sum()

created_at         0
id                 0
text               0
user_id            0
omicron_tweets     0
clean_text         0
compound           0
neg                0
neu                0
pos                0
week               0
UIN                0
clean_text2        0
tokenised_tweet    0
lemmatized         0
lemma_2            0
dtype: int64

In [ ]:
df_cleanT.info()

In [ ]:
#df_cleanT = df_cleanT.dropna()

In [ ]:
df_cleanT.head()

In [ ]:
df_cleanT.tail()

In [ ]:
len(df_cleanT['id'])

In [ ]:
all_topics =  ['symptoms','prevention', 'testing', 'treatment', 'economic_impact', 'travel', 'vaccination', 'vaccination_opposition', 
 'policies', 'causes', 'transmission', 'children_education', 'government', 'mental_health']


tab, words = corex_func_anchor(df_cleanT)



In [ ]:
df_result = pd.DataFrame(tab, columns = all_topics, index=df_cleanT.index)
df_result = round(df_result, 6)
df_result.head(1000)

#df_cor = corex_func_anchor(df)
#df_cor

symptoms  prevention    testing  treatment  economic_impact     travel  \
0   -19.506433  -19.751329 -18.552575 -16.700710       -18.382905 -17.621016   
1   -18.501173  -19.742700 -20.586028 -15.673633       -18.396170 -17.584599   
2   -18.966519  -19.744439 -18.582778 -16.715123       -18.392439 -17.589077   
3   -18.221525  -19.750917 -18.020274 -16.713945       -17.155064 -17.577657   
4   -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   
5   -18.966519  -19.750701 -18.582778 -16.713466       -18.392241 -17.588992   
6   -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   
7   -18.966520  -19.750753 -18.582778 -16.713378       -18.391611 -17.588923   
8   -18.966520  -18.847482 -18.582778 -16.713368       -18.453602 -17.588923   
9   -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   
10  -18.966501  -19.738050 -18.582778 -17.568283       -18.391976 -17.591619   
11    0.000000  -19.751259 -17.706210 -16.670173       -17.162147 -14.551265   
12  -18.966530  -19.750768 -18.582784 -16.725654       -18.413238 -17.589004   
13  -19.506497  -19.750826 -18.071042 -16.684319       -17.188680 -17.579005   
14  -14.877894  -19.752005 -18.071638 -16.799717       -18.414272 -17.470809   
15  -18.222264  -19.750920 -18.020274 -16.712662       -17.154905 -17.579025   
16  -17.605491  -19.751045 -17.363250 -16.712427       -18.397891 -17.557742   
17  -19.506418  -19.750739 -18.582825 -15.517790       -18.392282 -17.588934   
18  -18.966889  -16.747880 -18.591834 -16.717259       -18.391427 -17.589001   
19  -18.966520  -19.750746 -18.582778 -16.713360       -18.277238 -17.588982   
20  -17.605485  -19.751147 -16.851515 -16.700358       -17.160081 -17.547592   
21  -18.967500  -19.751655 -24.374666 -16.721077       -17.174757 -17.581116   
22  -19.506493  -19.750750 -19.093986 -16.714390       -18.395622 -17.597793   
23  -19.506422  -19.750743 -18.582778 -16.713366       -18.391353 -17.588922   
24  -18.966583  -19.751088 -18.068943 -15.494650       -18.389490 -17.583954   
25  -18.966521  -19.750697 -18.532010 -16.713832       -18.394280 -17.589169   
26  -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   
27  -15.795892  -19.751539 -15.838408 -16.712849       -17.163497 -15.971000   
28  -18.934479  -18.624315 -18.071042 -16.716116       -18.392689 -17.584414   
29  -18.222262  -19.707309 -18.152372 -16.713278       -18.393120 -17.588170   
30    0.000000  -19.751259 -17.706210 -16.670173       -17.162147 -14.551265   
31    0.000000  -19.751259 -17.706210 -16.670173       -17.162147 -14.551265   
32  -17.965795  -19.750818 -18.582821 -16.714540       -18.394666 -17.592760   
33  -18.966589  -19.750771 -18.071047 -16.715061       -18.394540 -17.584416   
34  -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   
35  -18.966519  -19.750753 -18.582800 -16.713398       -18.277071 -17.588933   
36  -18.919011  -18.656079 -18.582778 -16.713668       -18.394252 -17.589262   
37  -17.405453  -19.750373 -18.020285 -16.711591       -17.155835 -17.579389   
38  -18.173432  -19.750851 -18.020274 -16.713761       -18.246193 -17.584767   
39  -17.605525  -19.751801 -16.851515 -16.696198        -1.331914 -17.547521   
40  -17.243360  -19.751105 -18.582778 -16.792650       -18.403820 -17.585675   
41  -18.966542  -19.750774 -18.582784 -16.731946       -18.425496 -17.589083   
42  -19.506492  -19.750890 -16.671074 -16.715011       -18.391651   0.000000   
43  -18.222264  -19.750920 -18.020274 -16.712662       -17.154905 -17.579025   
44  -17.603756  -16.922010 -16.017410 -16.701704         0.000000 -17.548671   
45  -17.205750  -19.750813 -18.582781 -16.715278       -18.420273 -17.589232   
46  -18.850848  -19.749801 -18.071042 -15.592664       -11.013940 -17.585900   
47  -15.990938  -19.751379 -17.024133 -16.717764       -18.400498 -17.590671   
48  -18.966685  -19.751693 -18.582852 -16.720084       -18.393566 -17.590192   
49  -1

In [ ]:
df_result.tail(100)

symptoms  prevention    testing  treatment  economic_impact  \
441548 -19.506423  -19.750782 -18.582778 -16.713873       -18.394251   
441549 -15.928497  -19.680846 -18.071042 -16.713151       -18.385612   
441550 -19.506449  -19.205568 -18.583096 -15.266293       -14.693255   
441551 -19.506423  -19.750782 -18.582778 -16.713873       -18.394251   
441552 -18.966521  -18.109762 -18.071018   0.000000       -18.394097   
441553 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441554 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441555 -17.847697  -19.750197 -19.722652 -16.713883       -15.127248   
441556 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441557 -18.898660  -19.750764 -18.582800 -16.712514       -18.395219   
441558 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441559 -19.506415  -19.751043 -18.071044   0.000000       -18.390050   
441560 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441561 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441562 -16.667467  -19.737203 -16.427636 -16.721884       -18.246383   
441563 -19.506423  -19.750782 -18.582778 -16.713873       -18.394251   
441564 -18.966521  -19.750795 -18.582778 -16.715503         0.000000   
441565 -19.506423  -19.750782 -18.582778 -16.713873       -18.394251   
441566 -19.509522  -19.751309 -16.489594 -16.714347       -18.391694   
441567 -19.497686  -18.866736 -15.909419   0.000000       -18.394419   
441568 -18.966511  -19.750771 -18.582778   0.000000       -18.391277   
441569 -18.966521  -19.750794 -18.582778 -16.715518         0.000000   
441570 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441571 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441572 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441573 -19.506424  -19.750977 -18.071043   0.000000       -18.392390   
441574 -17.749265  -17.972611   0.000000  -0.199797       -18.394959   
441575 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441576 -18.397541  -19.750800 -18.582778 -16.701224       -18.390819   
441577 -15.372247  -19.683456 -18.582778   0.000000       -18.391420   
441578 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441579   0.000000  -19.750809 -18.582777 -16.710981       -18.392467   
441580 -19.506424  -19.750799 -18.582778 -16.714496       -18.395926   
441581 -18.966511  -19.750777 -18.582778   0.000000       -18.391523   
441582 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441583 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441584 -18.892475  -19.729017 -18.582778 -16.728361       -18.399837   
441585 -19.506424  -19.750799 -18.582778 -16.714496       -18.395926   
441586 -18.966511  -19.750777 -18.582778   0.000000       -18.391523   
441587 -18.966511  -19.750777 -18.582778   0.000000       -18.391523   
441588 -19.004680  -19.749264 -18.582820 -16.716145       -18.322953   
441589 -19.506423  -19.750785 -18.582778 -16.714231       -18.395667   
441590 -19.506423  -19.750767 -18.071042   0.000000       -18.335333   
441591 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441592 -18.968815  -19.750777 -17.802797   0.000000       -18.391557   
441593 -13.708629  -19.752163 -18.071042 -16.713308       -17.261200   
441594 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441595 -19.506423  -19.750785 -18.582778 -16.714231       -18.395667   
441596 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441597 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441598 -19.506428  -19.750819 -18.582778 -16.714554       -18.395881   
441599 -18.761739  -19.752416 -18.584485   0.000000       -18.384685   
441600 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441601 -19.506428  -19.750819 -18.582778 -16.714554       -18.395881   
441602 -16.906770  -18.805477 -18.582778 -16.7133

In [ ]:
df_cleanT['UIN'].head()

0    1
1    2
2    3
3    4
4    5
Name: UIN, dtype: int64

In [ ]:
df_result.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 441647 entries, 0 to 441647
Data columns (total 15 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   symptoms                441647 non-null  float64
 1   prevention              441647 non-null  float64
 2   testing                 441647 non-null  float64
 3   treatment               441647 non-null  float64
 4   economic_impact         441647 non-null  float64
 5   travel                  441647 non-null  float64
 6   vaccination             441647 non-null  float64
 7   vaccination_opposition  441647 non-null  float64
 8   policies                441647 non-null  float64
 9   causes                  441647 non-null  float64
 10  transmission            441647 non-null  float64
 11  children_education      441647 non-null  float64
 12  government              441647 non-null  float64
 13  mental_health           441647 non-null  float64
 14  Tweet_topic         

In [ ]:

#df_result['week'] = df_cleanT['week']

In [ ]:
#df_result['UIN'] = df_cleanT['UIN'].astype(int)

In [ ]:
#df_final_result = pd.concat([df_result, df_cleanT[['UIN', 'week', 'id']]], axis =1)

In [ ]:
#df_sample2 = df_result.iloc[0:1500]
max_ValueInd = df_result.idxmax(axis=1)
df_result['Tweet_topic'] = max_ValueInd
df_result.head(1000)
df_result['Tweet_topic'].value_counts()

In [ ]:
df_result.head()

symptoms  prevention    testing  treatment  economic_impact     travel  \
0 -19.506433  -19.751329 -18.552575 -16.700710       -18.382905 -17.621016   
1 -18.501173  -19.742700 -20.586028 -15.673633       -18.396170 -17.584599   
2 -18.966519  -19.744439 -18.582778 -16.715123       -18.392439 -17.589077   
3 -18.221525  -19.750917 -18.020274 -16.713945       -17.155064 -17.577657   
4 -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   

   vaccination  vaccination_opposition   policies     causes  transmission  \
0   -19.633975              -16.830359 -15.772993 -13.141060    -29.234769   
1   -21.438131              -16.901641 -16.532004  -9.812218    -17.889311   
2   -21.202835              -16.873421 -15.772543 -13.622427    -19.033638   
3   -21.448191              -16.895501 -15.772619 -15.295685    -18.886917   
4   -21.202835              -16.872438 -15.772536 -15.292150    -18.317507   

   children_education  government  mental_health    Tweet_topic  
0          -18.853736  -15.575138     -14.592570         causes  
1          -20.656190  -15.611936     -14.424977         causes  
2          -20.650097  -15.613493     -14.264499         causes  
3          -20.682621  -15.611348     -13.327366  mental_health  
4          -20.649263  -15.613733     -14.298353  mental_health

In [ ]:
df_result.shape

(441647, 15)

In [ ]:
df_cleanT.shape

(441647, 16)

In [ ]:
df_cleanT.columns

Index(['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos', 'week', 'UIN', 'clean_text2',
       'tokenised_tweet', 'lemmatized', 'lemma_2'],
      dtype='object')

In [ ]:
df_result.columns

Index(['symptoms', 'prevention', 'testing', 'treatment', 'economic_impact',
       'travel', 'vaccination', 'vaccination_opposition', 'policies', 'causes',
       'transmission', 'children_education', 'government', 'mental_health',
       'Tweet_topic'],
      dtype='object')

In [ ]:
df_final_result = pd.concat([df_result, df_cleanT[['UIN', 'week', 'id','clean_text', 'user_id', 'compound', 'lemma_2']]], axis =1)



In [ ]:
df_final_result['Sentiment_Class']=''
df_final_result.loc[df_final_result.compound >= 0.05,'Sentiment_Class']='Positive'
df_final_result.loc[(df_final_result.compound< 0.05) & (df_final_result.compound > -0.05),'Sentiment_Class']='Neutral'
df_final_result.loc[df_final_result.compound <= -0.05,'Sentiment_Class']='Negative'

In [ ]:
df_final_result = df_final_result[['id', 'UIN', 'week', 'user_id', 'clean_text', 'compound', 'lemma_2', 'symptoms', 'prevention', 'testing', 'treatment', 'economic_impact',
       'travel', 'vaccination', 'vaccination_opposition', 'policies', 'causes',
       'transmission', 'children_education', 'government', 
       'mental_health', 'Tweet_topic', 'Sentiment_Class']]

In [ ]:
df_final_result.tail()

id     UIN     week       user_id  \
441643   1.488377083076264e+18  441772  week_11  9.821061e+17   
441644  1.4883771069920335e+18  441773  week_11  2.855330e+09   
441645  1.4883773968058368e+18  441774  week_11  1.521389e+08   
441646  1.4883771493084815e+18  441775  week_11  1.441500e+18   
441647  1.4883777565262067e+18  441776  week_11  1.218511e+08   

                                                                                                                                                                                           clean_text  \
441643                                                                                                      ivermectin has antiviral effect against omicron and all other mutant strains of covid19     
441644                                                                                                      correctedjapans kowa says ivermectin showed antiviral effect against omicron in research    
441645                                                                                                                                   2 new omicron symptoms you wont realize are from covid  via    
441646                                                                        covid19 omicron variant now dominant in italy health body says  reuters  published at 20220114t120900z sourcereuters      
441647  good grief    wheres the logic in this      ‘south africans who test positive for the coronavirus but show no symptoms of covid19 will no longer be required to selfisolate  covid omicron      

        compound  \
441643   -0.2960   
441644    0.0000   
441645    0.0000   
441646    0.0000   
441647   -0.5346   

                                                                                                                                lemma_2  \
441643                                                                        ivermectin antiviral effect omicron mutant strain covid19   
441644                                                       correctedjapans kowa say ivermectin show antiviral effect omicron research   
441645                                                                                     2 new omicron symptom wont realize covid via   
441646                            covid19 omicron variant dominant italy health body say reuters publish 20220114t120900z sourcereuters   
441647  good grief wheres logic south african test positive coronavirus show symptoms covid19 longer required selfisolate covid omicron   

         symptoms  prevention    testing  treatment  economic_impact  \
441643 -18.761206  -19.750391 -18.582780   0.000000       -18.391308   
441644 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441645   0.000000  -19.750743 -18.532010 -16.713731       -18.392362   
441646 -18.394451  -19.753105 -18.601017 -15.501036       -18.430251   
441647 -13.598793  -17.174329   0.000000 -25.599746       -18.499403   

           travel  vaccination  vaccination_opposition   policies     causes  \
441643 -17.589022   -21.202835              -16.902390 -15.772587 -15.317714   
441644 -17.589179   -20.596543              -16.873360 -15.772476 -15.300565   
441645 -17.589187   -20.393116              -16.868576 -15.772537 -15.299558   
441646 -17.587727   -22.429805              -16.942949 -15.777533 -15.405632   
441647 -17.520330   -20.851873              -16.881507 -15.717047 -15.266708   

        transmission  children_education  government  mental_health  \
441643    -18.317359          -20.652750  -15.613762     -12.614011   
441644    -18.317507          -20.644349  -15.600154     -14.326632   
441645    -16.597002          -20.649599  -15.613737     -14.325061   
441646    -23.505778          -20.667826  -14.852081     -14.663270   
441647    -17.623691          -20.650209  -15.539560     -14.275912   

          Tweet_topic Sentiment_Class  
441643      treatment        Negative  
441644      treatment         Neutral  
441645       

In [ ]:
df_final_result.head()

id  UIN    week       user_id  \
0   1.462294248007504e+18    1  week_1  1.634359e+07   
1   1.464265614994952e+18    2  week_1  1.754451e+07   
2    1.46429253197022e+18    3  week_1  4.321370e+07   
3  1.4642925246678548e+18    4  week_1  2.719413e+07   
4  1.4642925159016776e+18    5  week_1  1.336693e+18   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound  \
0    0.7253   
1   -0.2996   
2    0.2500   
3   -0.0516   
4    0.0000   

                                                                                         lemma_2  \
0               nice join initiation first person chapter hold since world close covid19 calgary   
1  new novel coronavirus sarscov2 covid19 variant couldnt easy like kappa lambda omicron even pi   
2                                                                          put away joke omicron   
3                            break designate new coronavirus strain variant concern name omicron   
4                                                                                        omicron   

    symptoms  prevention    testing  treatment  economic_impact     travel  \
0 -19.506433  -19.751329 -18.552575 -16.700710       -18.382905 -17.621016   
1 -18.501173  -19.742700 -20.586028 -15.673633       -18.396170 -17.584599   
2 -18.966519  -19.744439 -18.582778 -16.715123       -18.392439 -17.589077   
3 -18.221525  -19.750917 -18.020274 -16.713945       -17.155064 -17.577657   
4 -18.966520  -19.750755 -18.582778 -16.713370       -18.391627 -17.588923   

   vaccination  vaccination_opposition   policies     causes  transmission  \
0   -19.633975              -16.830359 -15.772993 -13.141060    -29.234769   
1   -21.438131              -16.901641 -16.532004  -9.812218    -17.889311   
2   -21.202835              -16.873421 -15.772543 -13.622427    -19.033638   
3   -21.448191              -16.895501 -15.772619 -15.295685    -18.886917   
4   -21.202835              -16.872438 -15.772536 -15.292150    -18.317507   

   children_education  government  mental_health    Tweet_topic  \
0          -18.853736  -15.575138     -14.592570         causes   
1          -20.656190  -15.611936     -14.424977         causes   
2          -20.650097  -15.613493     -14.264499         causes   
3          -20.682621  -15.611348     -13.327366  mental_health   
4          -20.649263  -15.613733     -14.298353  mental_health   

  Sentiment_Class  
0        Positive  
1        Negative  
2        Positive  
3        Negative  
4         Neutral

In [ ]:
df_result.tail()

symptoms  prevention    testing  treatment  economic_impact  \
441643 -18.761206  -19.750391 -18.582780   0.000000       -18.391308   
441644 -18.966511  -19.750777 -18.582778   0.000000       -18.391420   
441645   0.000000  -19.750743 -18.532010 -16.713731       -18.392362   
441646 -18.394451  -19.753105 -18.601017 -15.501036       -18.430251   
441647 -13.598793  -17.174329   0.000000 -25.599746       -18.499403   

           travel  vaccination  vaccination_opposition   policies     causes  \
441643 -17.589022   -21.202835              -16.902390 -15.772587 -15.317714   
441644 -17.589179   -20.596543              -16.873360 -15.772476 -15.300565   
441645 -17.589187   -20.393116              -16.868576 -15.772537 -15.299558   
441646 -17.587727   -22.429805              -16.942949 -15.777533 -15.405632   
441647 -17.520330   -20.851873              -16.881507 -15.717047 -15.266708   

        transmission  children_education  government  mental_health  \
441643    -18.317359          -20.652750  -15.613762     -12.614011   
441644    -18.317507          -20.644349  -15.600154     -14.326632   
441645    -16.597002          -20.649599  -15.613737     -14.325061   
441646    -23.505778          -20.667826  -14.852081     -14.663270   
441647    -17.623691          -20.650209  -15.539560     -14.275912   

          Tweet_topic  
441643      treatment  
441644      treatment  
441645       symptoms  
441646  mental_health  
441647        testing

In [ ]:
df_final_result[df_final_result.isnull().any(axis=1)]

Empty DataFrame
Columns: [id, UIN, week, user_id, clean_text, compound, lemma_2, symptoms, prevention, testing, treatment, economic_impact, travel, vaccination, vaccination_opposition, policies, causes, transmission, children_education, government, mental_health, Tweet_topic, Sentiment_Class]
Index: []

In [ ]:
df_final_result.loc[441451]

id                                                                                                                                   1.4883555117035397e+18
UIN                                                                                                                                                  441580
week                                                                                                                                                week_11
user_id                                                                                                                                        3455710574.0
clean_text                ‼india reports 167  lac covid cases in last 24 hours ‼  1192 deaths  increasing day by day  covid19  omicron   please be safe 😷  
compound                                                                                                                                             0.6369
lemma_2                                                india rep

### Final Result stored in "Corex_result_Set2.csv" file

In [ ]:
df_final_result.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/Corex_result_Set2.csv")

### Analysis of the results: coming soon..


In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_2'].tail(100)
df_s.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/Sample_result/sample_Corex_result2.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_3'].tail(100)
df_s.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/Sample_result/sample_Corex_result3.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_5'].tail(100)
df_s.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/Sample_result/sample_Corex_result5.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_8'].tail(100)
df_s.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/Sample_result/sample_Corex_result.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_11'].tail(100)
df_s.to_csv("/content/drive/MyDrive/Omicron Tweet Analytics project/Filter7_res/Sample_result/sample_Corex_result11.csv")